In [1]:
    import matplotlib.pyplot as plt
    from mpl_toolkits.mplot3d import Axes3D
    import numpy as np
    import pandas as pd
    from scipy.spatial import cKDTree
    from math import sqrt, ceil
    from scipy.stats import linregress
    import math 
    import libraries as lib    

In [2]:
# Set file path
file_path = "C:/Users/qvled/OneDrive - HvA/Clean_Mobility_Files/H2A/Data voor hoogteprofiel.txt"

# Read GPS data
df = lib.lees_gps_data(file_path)

# Print the resulting DataFrame
df


timestamp   latitude lat_direction  longitude lon_direction  hoogte  \
0      063448.30  43.771393             N  -0.042098             W    99.5   
1      063448.40  43.771393             N  -0.042098             W    99.5   
2      063448.50  43.771393             N  -0.042098             W    99.4   
3      063448.60  43.771393             N  -0.042098             W    99.5   
4      063448.70  43.771393             N  -0.042098             W    99.4   
...          ...        ...           ...        ...           ...     ...   
46568       None  43.771202             N  -0.041941             W    96.0   
46569       None  43.771202             N  -0.041941             W    96.0   
46570       None  43.771202             N  -0.041941             W    96.1   
46571       None  43.771202             N  -0.041941             W    96.1   
46572       None  43.771202             N  -0.041941             W    96.2   

       speed_m/s  
0       0.038583  
1       0.026237  
2       0.035497  
3       0.073051  
4       0.064820  
...          ...  
46568        NaN  
46569        NaN  
46570        NaN  
46571        NaN  
46572        NaN  

[46573 rows x 7 columns]

In [3]:
#Filter vanaf het moment dat de auto de baan opgaat en wanneer die er weer afgaat.

# Definieer de coördinaten voor het start- en eindpunt
start_lon = -0.0446
start_lat = 0.00095 + 4.3771e1
end_lon = -0.039925
end_lat = 0.000300 + 4.3771e1

# Veronderstel dat 'df' je DataFrame is met de relevante data
filtered_df = lib.filter_track_data(df, start_lon, start_lat, end_lon, end_lat)

# Print het gefilterde DataFrame om te controleren
filtered_df
#43.767914, -0.035855

timestamp   latitude lat_direction  longitude lon_direction  hoogte  \
22340  071203.60  43.771951             N  -0.044597             W   102.0   
22341  071203.70  43.771954             N  -0.044603             W   102.0   
22342  071203.80  43.771955             N  -0.044609             W   102.0   
22343  071203.90  43.771958             N  -0.044616             W   102.0   
22344  071204.00  43.771960             N  -0.044622             W   102.0   
...          ...        ...           ...        ...           ...     ...   
42943  074720.40  43.771037             N  -0.040149             W    98.1   
42944  074720.50  43.771032             N  -0.040142             W    98.1   
42945  074720.60  43.771027             N  -0.040135             W    98.1   
42946  074720.70  43.771022             N  -0.040127             W    98.1   
42947  074720.80  43.771017             N  -0.040120             W    98.1   

       speed_m/s  
22340   5.597156  
22341   5.624421  
22342   5.633167  
22343   5.650143  
22344   5.655288  
...          ...  
42943   8.270209  
42944   8.298503  
42945   8.276382  
42946   8.287700  
42947   8.273810  

[20608 rows x 7 columns]

In [4]:
#Plot om te checken of het is gelukt en ref met maps
#Het is gelukt.

%matplotlib qt

# Definieer een functie voor een 2D-plot
def plot_2d_height_profile(latitudes, longitudes, hoogtes):
    plt.figure(figsize=(10, 6))
    scatter = plt.scatter(longitudes, latitudes, c=hoogtes, cmap='viridis', s=10, alpha=0.8)
    plt.scatter(-0.04204167, 43.77199, color='red', s=100, marker='o', label='Specifiek punt')
    plt.scatter(-0.04039667, 43.77055, color='red', s=100, marker='o', label='Specifiek punt')
    plt.colorbar(scatter, label='Hoogte (m)')
    plt.xlabel('Longitude')
    plt.ylabel('Latitude')
    plt.title('2D Hoogteprofiel')
    plt.grid(True)
    plt.show()

# Voorbeeld dataframe (hier kun je je eigen gefilterde data inladen)
# Gebruik de functie met de gefilterde data
plot_2d_height_profile(filtered_df['latitude'], filtered_df['longitude'], filtered_df['hoogte'])


In [5]:
import plotly.express as px
import plotly.graph_objects as go
import pandas as pd

def plot_2d_height_profile(latitudes, longitudes, hoogtes):
    # Voeg de index als een label toe
    indices = latitudes.index.astype(str)  # Omzetten naar string voor weergave

    fig = go.Figure(data=go.Scatter(
        x=longitudes,
        y=latitudes,
        mode='markers',
        marker=dict(
            size=5,
            color=hoogtes,
            colorscale='Viridis',
            colorbar_title='Hoogte (m)'
        ),
        hovertext=[f"Index: {index}<br>Hoogte: {hoogte:.2f} m" for index, hoogte in zip(indices, hoogtes)],
        hoverinfo='text'
    ))
    
    # Voeg specifieke punten toe
    fig.add_trace(go.Scatter(
        x=[-0.04204167, -0.04039667],
        y=[43.77199, 43.77055],
        mode='markers',
        marker=dict(
            size=10,
            color='red'
        ),
        name='Specifiek punt'
    ))

    fig.update_layout(
        title='2D Hoogteprofiel',
        xaxis_title='Longitude',
        yaxis_title='Latitude'
    )
    
    fig.show()

# Gebruik de functie met de gefilterde data
plot_2d_height_profile(filtered_df['latitude'], filtered_df['longitude'], filtered_df['hoogte'])


In [6]:
#Filter voor de rechte stukken.

# Set initial flag and empty list
gevonden = False
rechtestuk_rijen_hoogte = []

# Define the coordinates for the two rectangular areas
lat_min, lat_max = 7e-5 + 4.37724e1, 8.6e-5 + 4.37724e1
lon_min, lon_max = -0.04224, -0.04221

lat_min2, lat_max2 = 70e-5 + 4.377e1, 74e-5 + 4.377e1
lon_min2, lon_max2 = -0.03982, -0.03975


# Iterate over each row in the DataFrame (replace df with your actual DataFrame)
for i in range(len(filtered_df)):
    lat = filtered_df['latitude'].iloc[i]  # Latitude of the i-th row
    lon = filtered_df['longitude'].iloc[i]  # Longitude of the i-th row
   
    # Check if the point is within the first box
    if lat_min <= lat <= lat_max and lon_min <= lon <= lon_max:
        if not gevonden:  # Append only the first time a point is found in the first box
            rechtestuk_rijen_hoogte.append(i)
            gevonden = True  # Set 'gevonden' flag to True

    # Check if the point is within the second box after finding a point in the first box
    if gevonden and lat_min2 <= lat <= lat_max2 and lon_min2 <= lon <= lon_max2:
        rechtestuk_rijen_hoogte.append(i)
        gevonden = False  # Reset 'gevonden' flag to False after processing the second box
        
    #Optionally, you can print out each step to debug
    # print(f"i: {i}, lat: {lat}, lon: {lon}, gevonden: {gevonden}, rechtestuk_rijen: {rechtestuk_rijen}")

# Convert the list to a numpy array if needed

# Print the results
print("Indices of points in the two boxes:", rechtestuk_rijen_hoogte)


Indices of points in the two boxes: [962, 1282, 3058, 3356, 5066, 5370, 7068, 7372, 9238, 9561, 11378, 11698, 13580, 13908, 15782, 16107, 18039, 18370, 20317]


In [7]:
#Check of het is gelukt met de rechte stukken
#Het is gelukt
%matplotlib qt

import matplotlib.pyplot as plt

def plot_hoogteprofiel_2d(latitudes, longitudes, hoogtes):
    # Increase figure size by setting the figsize
    fig, ax = plt.subplots(figsize=(12, 8))  # Adjust the width and height as needed
    scatter = ax.scatter(longitudes, latitudes, c=hoogtes, cmap='viridis', marker='o')
    ax.set_title('Hoogteprofiel van racebaan Nogaro', fontsize=16)
    ax.set_xlabel('Longitude', fontsize=14)
    ax.set_ylabel('Latitude', fontsize=14)
    
    # Create the colorbar
    cbar = fig.colorbar(scatter, ax=ax)
    cbar.set_label('Hoogte boven zeeniveau (m)', fontsize=12)

    # Plot the rectangular boundaries
    plt.plot(
        [lon_min, lon_max, lon_max, lon_min, lon_min],
        [lat_min, lat_min, lat_max, lat_max, lat_min],
        color='red', linestyle='--', linewidth=2, label="Boundary Square")

    plt.plot(
        [lon_min2, lon_max2, lon_max2, lon_min2, lon_min2],
        [lat_min2, lat_min2, lat_max2, lat_max2, lat_min2],
        color='red', linestyle='--', linewidth=2, label="Boundary Square")

    for i in range(len(latitudes)):
        lat = latitudes.iloc[i]
        lon = longitudes.iloc[i]
        #plt.text(lon, lat, str(i), fontsize=8, color='black')

    # Enable grid
    plt.grid(True)
    
    # Show the plot
    plt.show()

# Assuming `df` is your DataFrame with columns: 'latitude', 'longitude', and 'hoogte'
plot_hoogteprofiel_2d(filtered_df['latitude'], filtered_df['longitude'], filtered_df['hoogte'])


In [8]:
#Check afstand tussen begin-en eindrij

# Voorbeeld van hoe de functie te gebruiken
# Stel dat filtered_df al je DataFrame is
row_index1 = 962+22340  # Vervang dit door de index van de eerste rij
row_index2 = 1282+22340  # Vervang dit door de index van de tweede rij

# Bereken de afstand tussen de twee punten
afstand = lib.calculate_distance_between_rows(filtered_df, row_index1, row_index2)
print(f"De afstand tussen rij {row_index1} en rij {row_index2} is: {afstand} meter")


De afstand tussen rij 23302 en rij 23622 is: 275.5040146481721 meter


In [9]:
# Bereken de afstand en hoogteverschil voor elke rij van 23302 tot en met 23622
rows = range(27855, 28225)
afstanden = []
hoogteverschillen = []

for i in range(len(rows) - 1):
    row_index1 = rows[i]
    row_index2 = rows[i + 1]
    
    # Bereken afstand en hoogteverschil
    afstand = lib.calculate_distance_between_rows(filtered_df, row_index1, row_index2)
    hoogteverschil = lib.calculate_height_difference(filtered_df, row_index1, row_index2)
    
    afstanden.append(afstand)
    hoogteverschillen.append(hoogteverschil)

# Maak een DataFrame met de resultaten
hoogte_vs_afstand = pd.DataFrame({
    'afstand': afstanden,
    'hoogteverschil': hoogteverschillen
})

# Voeg cumulatieve afstand en cumulatief hoogteverschil toe
hoogte_vs_afstand['cumulatieve_afstand'] = hoogte_vs_afstand['afstand'].cumsum()
hoogte_vs_afstand['cumulatief_hoogteverschil'] = hoogte_vs_afstand['hoogteverschil'].cumsum()

# Print de DataFrame
hoogte_vs_afstand


afstand  hoogteverschil  cumulatieve_afstand  cumulatief_hoogteverschil
0    0.388608             0.0             0.388608                        0.0
1    0.380928             0.0             0.769536                        0.0
2    0.739006             0.0             1.508542                        0.0
3    0.723744             0.0             2.232286                        0.0
4    0.358078             0.0             2.590364                        0.0
..        ...             ...                  ...                        ...
364  0.787384             0.0           201.940328                        1.0
365  1.609948             0.0           203.550276                        1.0
366  0.787384             0.0           204.337660                        1.0
367  0.787384             0.0           205.125044                        1.0
368  0.809826             0.0           205.934870                        1.0

[369 rows x 4 columns]

In [10]:
#hoogte vs afstand met fitvergelijking
hoogte_vs_afstand = pd.DataFrame(hoogte_vs_afstand)

# Data voor de plot
x = hoogte_vs_afstand['cumulatieve_afstand']
y = hoogte_vs_afstand['cumulatief_hoogteverschil']

# Zevende graads polynoomfit
degree = 7
coefficients_7 = np.polyfit(x, y, degree)
polynomial_7 = np.poly1d(coefficients_7)
y_fit_7 = polynomial_7(x)

# Plot de scatter en de fit
plt.figure(figsize=(10, 6))
plt.scatter(x, y, label='Data punten')
plt.plot(x, y_fit_7, color='purple', linestyle='-', linewidth=2, label=f'Beste fit (graad {degree})')

# Formule van de polynoomfit genereren
fit_equation_7 = "y = " + " + ".join(
    [f"{coef:.2e}x^{degree - i}" if degree - i > 0 else f"{coef:.2e}" for i, coef in enumerate(coefficients_7)]
)

# Formule toevoegen aan de plot
plt.text(
    0.05 * max(x),
    0.85 * max(y),
    fit_equation_7,
    color='purple',
    fontsize=10,
    bbox=dict(facecolor='white', alpha=0.6)
)

# Labels en titel
plt.xlabel('Cumulatieve Afstand (m)', fontsize=14)
plt.ylabel('Cumulatief Hoogteverschil (m)', fontsize=14)
plt.title('Cumulatief Hoogteverschil vs. Cumulatieve Afstand', fontsize=16)
plt.grid(visible=True, linestyle='--', alpha=0.7)
plt.legend(fontsize=12, loc='lower left')
plt.tight_layout()
plt.show()

# Print de formule
print(fit_equation_7)


y = -5.75e-17x^7 + 6.92e-14x^6 + -2.48e-11x^5 + 3.61e-09x^4 + -2.02e-07x^3 + 7.62e-06x^2 + 3.53e-03x^1 + 5.36e-02


In [11]:
#formule voor h, pas x_fit aan om het aantal datapunten te veranderen
x_fit = np.linspace(0, 206, 369)
h = polynomial_7(x_fit)

# Plot the fit equation from x = 0 to x = 275
plt.figure(figsize=(10, 6))
plt.plot(x_fit, h, color='purple', linestyle='-', linewidth=2, label=f'Polynoom fit (graad {degree})')
plt.grid(visible=True, linestyle='--', alpha=0.7)
#Add fit equation to the plot
plt.text(
    0.05 * max(x_fit),
    0.85 * max(y_fit_7),
    fit_equation_7,
    color='purple',
    fontsize=10,
    bbox=dict(facecolor='white', alpha=0.7)
)
plt.xlabel('Cumulatieve Afstand (m)', fontsize=14)
plt.ylabel('Cumulatief Hoogteverschil (m)', fontsize=14)
plt.title('Fit voor hoogte profiel rechte stuk met vermogen', fontsize=16)

plt.show()

In [12]:
#Inladen motordriver

directory = "C:/Users\qvled\OneDrive - HvA\Logfiles\H2A/2023/Nogaro/20230525_h2a_poging1/0002/"
file_motordriver ="5.csv"
data_file_motordriver = lib.DataInladenMotorDriver(f'{directory}{file_motordriver}')

#Fix de longitude
data_file_motordriver["GPS longitude, in graden"] = data_file_motordriver["GPS longitude, in graden"]* -1

#Voeg wielsnelheid in m/s toe
data_file_motordriver.loc[:, "Wielsnelheid, in m/s"] = data_file_motordriver["Wielsnelheid, in km/h"] / 3.6

data_file_motordriver.loc[:, "GPS speed, in m/s"] = data_file_motordriver["GPS speed, in km/h"] / 3.6


In [13]:
# Handmatige specificatie van start- en eindrij
start_row = 223257  # Begin vanaf rij 223257
end_row = 479444    # Eindig bij rij 250000

# Filter de data
filtered_motordriver = lib.filter_track_data_with_start_and_end(data_file_motordriver, start_row, end_row)

# Print het gefilterde DataFrame
filtered_motordriver


Datalogger port  Dataloggertijd, in s Format header (>03|04)  \
223257                5             4540.1490                  03|04   
223258                5             4540.1571                  03|04   
223259                5             4540.1652                  03|04   
223260                5             4540.1734                  03|04   
223261                5             4540.1815                  03|04   
...                 ...                   ...                    ...   
479440                5             6774.8277                  03|04   
479441                5             6774.8364                  03|04   
479442                5             6774.8451                  03|04   
479443                5             6774.8538                  03|04   
479444                5             6774.8625                  03|04   

        Tijd sinds laatste herstart motordriver (s)  \
223257                                     898.7554   
223258                                     898.7634   
223259                                     898.7716   
223260                                     898.7796   
223261                                     898.7878   
...                                             ...   
479440                                    3133.0471   
479441                                    3133.0559   
479442                                    3133.0647   
479443                                    3133.0735   
479444                                    3133.0820   

        Spanning over de motor (V)  Stroom door de motor (A)  \
223257                       2.689                     9.883   
223258                       3.127                    10.037   
223259                       3.702                    10.203   
223260                       3.541                    10.329   
223261                       3.242                    10.222   
...                            ...                       ...   
479440                       0.021                    -0.085   
479441                       0.020                    -0.084   
479442                       0.020                    -0.084   
479443                       0.020                    -0.083   
479444                       0.020                    -0.084   

        Vermogen geleverd aan de motor (W)  \
223257                                36.8   
223258                                43.2   
223259                                51.8   
223260                                50.1   
223261                                46.2   
...                                    ...   
479440                                -0.0   
479441                                -0.0   
479442                                -0.0   
479443                                -0.0   
479444                                -0.0   

        Energie geleverd aan de motor sinds reset (J)  \
223257                                          -1340   
223258                                          -1340   
223259                                          -1339   
223260                                          -1339   
223261                                          -1339   
...                                               ...   
479440                                         181490   
479441                                         181490   
479442                                         181490   
479443                                         181490   
479444                                         181490   

        Spanning aan de ingang van motordriver (V)  \
223257                                      31.898   
223258                                      31.894   
223259                                      31.889   
223260                                      31.889   
223261                                      31.894   
...                                            ...   
479440                                      30.445   
479441                                     

In [15]:
# Pas de functie toe op latitude en longitude kolommen, waarbij NaN-waarden worden behouden
filtered_motordriver['GPS latitude, in graden'] = filtered_motordriver['GPS latitude, in graden'].apply(lambda x: lib.convert_to_decimal_degrees2(x) if pd.notna(x) else None)
filtered_motordriver['GPS longitude, in graden'] = filtered_motordriver['GPS longitude, in graden'].apply(lambda x: -lib.convert_to_decimal_degrees2(abs(x)) if pd.notna(x) and x < 0 else lib.convert_to_decimal_degrees2(x) if pd.notna(x) else None)

filtered_motordriver

C:\Users\qvled\AppData\Local\Temp\ipykernel_20372\1517001316.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\qvled\AppData\Local\Temp\ipykernel_20372\1517001316.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



Datalogger port  Dataloggertijd, in s Format header (>03|04)  \
223257                5             4540.1490                  03|04   
223258                5             4540.1571                  03|04   
223259                5             4540.1652                  03|04   
223260                5             4540.1734                  03|04   
223261                5             4540.1815                  03|04   
...                 ...                   ...                    ...   
479440                5             6774.8277                  03|04   
479441                5             6774.8364                  03|04   
479442                5             6774.8451                  03|04   
479443                5             6774.8538                  03|04   
479444                5             6774.8625                  03|04   

        Tijd sinds laatste herstart motordriver (s)  \
223257                                     898.7554   
223258                                     898.7634   
223259                                     898.7716   
223260                                     898.7796   
223261                                     898.7878   
...                                             ...   
479440                                    3133.0471   
479441                                    3133.0559   
479442                                    3133.0647   
479443                                    3133.0735   
479444                                    3133.0820   

        Spanning over de motor (V)  Stroom door de motor (A)  \
223257                       2.689                     9.883   
223258                       3.127                    10.037   
223259                       3.702                    10.203   
223260                       3.541                    10.329   
223261                       3.242                    10.222   
...                            ...                       ...   
479440                       0.021                    -0.085   
479441                       0.020                    -0.084   
479442                       0.020                    -0.084   
479443                       0.020                    -0.083   
479444                       0.020                    -0.084   

        Vermogen geleverd aan de motor (W)  \
223257                                36.8   
223258                                43.2   
223259                                51.8   
223260                                50.1   
223261                                46.2   
...                                    ...   
479440                                -0.0   
479441                                -0.0   
479442                                -0.0   
479443                                -0.0   
479444                                -0.0   

        Energie geleverd aan de motor sinds reset (J)  \
223257                                          -1340   
223258                                          -1340   
223259                                          -1339   
223260                                          -1339   
223261                                          -1339   
...                                               ...   
479440                                         181490   
479441                                         181490   
479442                                         181490   
479443                                         181490   
479444                                         181490   

        Spanning aan de ingang van motordriver (V)  \
223257                                      31.898   
223258                                      31.894   
223259                                      31.889   
223260                                      31.889   
223261                                      31.894   
...                                            ...   
479440                                      30.445   
479441                                     

In [17]:
plt.figure(figsize=(10, 6))
plt.title('Motordriver GPS tegen Hoogteprofiel GPS')
plt.ylabel('Longitude')
plt.xlabel('Latitude')
plt.scatter(filtered_motordriver['GPS longitude, in graden'], filtered_motordriver['GPS latitude, in graden'], color ='r', label= 'Filtered_motordriver')
plt.scatter(filtered_df['longitude'], filtered_df['latitude'], color='b', label='Filtered DF')
plt.legend()
plt.grid(visible=True, linestyle='--', alpha=0.7)
plt.show()

In [19]:
import pandas as pd

# Voorbeeld dataframe 'finish' met gelijke lengtes voor alle kolommen
data = {
    'GPS latitude, in graden': [0.226 + 4.346e3, 0.237 + 4.346e3],
    'GPS longitude, in graden': [-2.4250, -2.4225],  # Longitude bevatte al negatieve waarden
    'Latitude richting': ['N', 'N'],
    'Longitude richting': ['W', 'W']
}

# Maak een DataFrame van de data
finish = pd.DataFrame(data)

# Pas de functie toe op latitude en longitude kolommen, waarbij NaN-waarden worden behouden
finish['GPS latitude, in graden'] = finish['GPS latitude, in graden'].apply(lambda x: lib.convert_to_decimal_degrees2(x) if pd.notna(x) else None)
finish['GPS longitude, in graden'] = finish['GPS longitude, in graden'].apply(lambda x: -lib.convert_to_decimal_degrees2(abs(x)) if pd.notna(x) and x < 0 else lib.convert_to_decimal_degrees2(x) if pd.notna(x) else None)

print(finish)


   GPS latitude, in graden  GPS longitude, in graden Latitude richting  \
0                43.770433                 -0.040417                 N   
1                43.770617                 -0.040375                 N   

  Longitude richting  
0                  W  
1                  W  


In [20]:
#Finish rijen

gevonden = False
finish_rijen = np.array([])

lat_min, lat_max = -0.040417, -0.040375
lon_min, lon_max = 43.770433, 43.770617 

# Kolomnamen
yas = 'GPS latitude, in graden'
xas = 'GPS longitude, in graden'
afstand_rondje = 1588.84925219  # Afstand van een rondje in meters

# Filter rows where latitude, longitude, and the distance are non-zero
filtered_motordriver = filtered_motordriver[filtered_motordriver[xas] != 0]
filtered_motordriver = filtered_motordriver[filtered_motordriver[yas] != 0]
filtered_motordriver = filtered_motordriver[filtered_motordriver['Afgelegde afstand sinds laatste herstart motordriver (m)'] != 0]

# Itereer over elke rij in de DataFrame
for i in range(len(filtered_motordriver)):
    lat = filtered_motordriver[xas].iloc[i]  # Latitude van de i-de rij
    lon = filtered_motordriver[yas].iloc[i]  # Longitude van de i-de rij
    afstand = filtered_motordriver["Afgelegde afstand sinds laatste herstart motordriver (m)"].iloc[i]

    # Controleer of het punt binnen het vierkant valt
    if lat_min <= lat <= lat_max and lon_min <= lon <= lon_max:
        if not gevonden:  # Voeg alleen toe als dit de eerste keer is dat we het punt vinden
            finish_rijen = np.append(finish_rijen, i)
            gevonden = True  # Vlag op 'gevonden' zetten
            start_afstand = afstand  # Opslaan van de startafstand bij het eerste punt

    # Controleer of de afgelegde afstand groter is dan een volledige ronde
    if gevonden and afstand >= start_afstand + (afstand_rondje * (len(finish_rijen))):
        finish_rijen = np.append(finish_rijen, i)

print(finish_rijen)
afstanden = np.array([])  # Maak een lege array voor afstanden


[ 26251.  49486.  74393. 100200. 124732. 149852. 174488. 200208. 226012.
 255494.]


In [23]:
#Check of het is gelukt met de rondes
#Het is gelukt
%matplotlib qt

def plot_hoogteprofiel_2d(latitudes, longitudes, hoogtes):
    # Increase figure size by setting the figsize
    fig, ax = plt.subplots(figsize=(12, 8))  # Adjust the width and height as needed
    scatter = ax.scatter(filtered_df['longitude'], filtered_df['latitude'], filtered_df['hoogte'], cmap='viridis', marker='o')
    ax.set_title('Hoogteprofiel van racebaan Nogaro', fontsize=16)
    ax.set_xlabel('Longitude', fontsize=14)
    ax.set_ylabel('Latitude', fontsize=14)
    
    # Create the colorbar
    cbar = fig.colorbar(scatter, ax=ax)
    cbar.set_label('Hoogte boven zeeniveau (m)', fontsize=12)

    # Plot the rectangular boundaries
    plt.plot(
        [lon_min, lon_max, lon_max, lon_min, lon_min],
        [lat_min, lat_min, lat_max, lat_max, lat_min],
        color='red', linestyle='--', linewidth=2, label="Boundary Square")

    for i in range(len(latitudes)):
        lat = latitudes.iloc[i]
        lon = longitudes.iloc[i]
        #plt.text(lon, lat, str(i), fontsize=8, color='black')

    # Enable grid
    plt.grid(True)
    
    # Show the plot
    plt.show()

# Assuming `df` is your DataFrame with columns: 'latitude', 'longitude', and 'hoogte'
plot_hoogteprofiel_2d(filtered_df['latitude'], filtered_df['longitude'], filtered_df['hoogte'])


C:\Users\qvled\AppData\Local\Temp\ipykernel_20372\3583403640.py:8: UserWarning:

No data for colormapping provided via 'c'. Parameters 'cmap' will be ignored



In [24]:
#Maken df's per ronde motordriver
begin_eind_paren2 = [
    (0, 26251), 
    (26251, 49486), 
    (49486, 74393), 
    (74393, 100200),
    (100200, 124732), 
    (124732, 149852), 
    (149852, 174488), 
    (174488, 200208),
    (200208, 226012), 
    (226012, 255494)
]

# Maak een lege lijst om de rondes-dataframes op te slaan
rondes = []

# Loop door elke (begin, eind) paar en maak een DataFrame subset
for i, (begin, eind) in enumerate(begin_eind_paren2):
    df_segment = filtered_motordriver.iloc[begin:eind]
    rondes.append(df_segment)

# Je kunt nu elke ronde benaderen als rondes[0], rondes[1], etc.
df_ronde1 = rondes[0]
df_ronde2 = rondes[1]
df_ronde3 = rondes[2]
df_ronde4 = rondes[3]
df_ronde5 = rondes[4]
df_ronde6 = rondes[5]
df_ronde7 = rondes[6]
df_ronde8 = rondes[7]
df_ronde9 = rondes[8]
df_ronde10 = rondes[9]

# Print het resultaat voor de eerste ronde om te controleren
df_ronde6


Datalogger port  Dataloggertijd, in s Format header (>03|04)  \
347989                5             5617.1410                  03|04   
347990                5             5617.1498                  03|04   
347991                5             5617.1586                  03|04   
347992                5             5617.1674                  03|04   
347993                5             5617.1761                  03|04   
...                 ...                   ...                    ...   
373104                5             5837.5367                  03|04   
373105                5             5837.5455                  03|04   
373106                5             5837.5543                  03|04   
373107                5             5837.5631                  03|04   
373108                5             5837.5720                  03|04   

        Tijd sinds laatste herstart motordriver (s)  \
347989                                    1975.5612   
347990                                    1975.5699   
347991                                    1975.5789   
347992                                    1975.5876   
347993                                    1975.5964   
...                                             ...   
373104                                    2195.9187   
373105                                    2195.9275   
373106                                    2195.9363   
373107                                    2195.9453   
373108                                    2195.9541   

        Spanning over de motor (V)  Stroom door de motor (A)  \
347989                      20.513                     8.113   
347990                      20.556                     8.133   
347991                      20.435                     8.116   
347992                      20.648                     8.120   
347993                      20.702                     8.080   
...                            ...                       ...   
373104                      21.498                     8.001   
373105                      21.908                     8.061   
373106                      21.476                     8.042   
373107                      21.311                     8.051   
373108                      21.393                     8.014   

        Vermogen geleverd aan de motor (W)  \
347989                               178.6   
347990                               179.8   
347991                               179.4   
347992                               180.6   
347993                               180.2   
...                                    ...   
373104                               182.8   
373105                               187.0   
373106                               184.1   
373107                               182.8   
373108                               181.9   

        Energie geleverd aan de motor sinds reset (J)  \
347989                                          96685   
347990                                          96686   
347991                                          96688   
347992                                          96689   
347993                                          96691   
...                                               ...   
373104                                         114180   
373105                                         114182   
373106                                         114183   
373107                                         114185   
373108                                         114187   

        Spanning aan de ingang van motordriver (V)  \
347989                                      27.494   
347990                                      27.493   
347991                                      27.492   
347992                                      27.491   
347993                                      27.489   
...                                            ...   
373104                                      27.361   
373105                                     

In [25]:
#Filter voor recht stuk in ronde 6

# Set initial flag and empty list
gevonden = False
rechtestuk_rijen_hoogte = []

# Define the coordinates for the two rectangular areas
lat_min, lat_max = 7e-5 + 4.37724e1, 8.6e-5 + 4.37724e1
lon_min, lon_max = -0.04224, -0.04221

lat_min2, lat_max2 = 70e-5 + 4.377e1, 74e-5 + 4.377e1
lon_min2, lon_max2 = -0.03982, -0.03975


# Iterate over each row in the DataFrame (replace df with your actual DataFrame)
for i in range(len(df_ronde6)):
    lat = df_ronde6['GPS latitude, in graden'].iloc[i]  # Latitude of the i-th row
    lon = df_ronde6['GPS longitude, in graden'].iloc[i]  # Longitude of the i-th row
   
    # Check if the point is within the first box
    if lat_min <= lat <= lat_max and lon_min <= lon <= lon_max:
        if not gevonden:  # Append only the first time a point is found in the first box
            rechtestuk_rijen_hoogte.append(i)
            gevonden = True  # Set 'gevonden' flag to True

    # Check if the point is within the second box after finding a point in the first box
    if gevonden and lat_min2 <= lat <= lat_max2 and lon_min2 <= lon <= lon_max2:
        rechtestuk_rijen_hoogte.append(i)
        gevonden = False  # Reset 'gevonden' flag to False after processing the second box
        
    #Optionally, you can print out each step to debug
    # print(f"i: {i}, lat: {lat}, lon: {lon}, gevonden: {gevonden}, rechtestuk_rijen: {rechtestuk_rijen}")

# Convert the list to a numpy array if needed

# Print the results
print("Indices of points in the two boxes:", rechtestuk_rijen_hoogte)



Indices of points in the two boxes: [18594, 22484]


In [26]:
import plotly.express as px
import pandas as pd

# Maak een nieuw dataframe voor het rechte stuk
rechte_stuk_ronde5_ronde6 = filtered_motordriver.loc[347364:350479]

# Voorbeeld van het maken van de scatterplot met de index als hover
fig = px.scatter(
    rechte_stuk_ronde5_ronde6,
    x='GPS longitude, in graden',
    y='GPS latitude, in graden',
    hover_name=rechte_stuk_ronde5_ronde6.index.astype(str),  # Index informatie tonen bij hover
    title='GPS Scatter Plot'
)

# Plot weergeven
fig.show()


In [40]:
rechte_stuk_ronde5_ronde6

Datalogger port  Dataloggertijd, in s Format header (>03|04)  \
347989                5             5617.1410                  03|04   
347990                5             5617.1498                  03|04   
347991                5             5617.1586                  03|04   
347992                5             5617.1674                  03|04   
347993                5             5617.1761                  03|04   
...                 ...                   ...                    ...   
350475                5             5638.9669                  03|04   
350476                5             5638.9757                  03|04   
350477                5             5638.9845                  03|04   
350478                5             5638.9933                  03|04   
350479                5             5639.0022                  03|04   

        Tijd sinds laatste herstart motordriver (s)  \
347989                                    1975.5612   
347990                                    1975.5699   
347991                                    1975.5789   
347992                                    1975.5876   
347993                                    1975.5964   
...                                             ...   
350475                                    1997.3832   
350476                                    1997.3922   
350477                                    1997.4010   
350478                                    1997.4098   
350479                                    1997.4186   

        Spanning over de motor (V)  Stroom door de motor (A)  \
347989                      20.513                     8.113   
347990                      20.556                     8.133   
347991                      20.435                     8.116   
347992                      20.648                     8.120   
347993                      20.702                     8.080   
...                            ...                       ...   
350475                      22.547                     6.730   
350476                      22.042                     6.672   
350477                      22.190                     6.824   
350478                      21.737                     6.666   
350479                      21.627                     6.497   

        Vermogen geleverd aan de motor (W)  \
347989                               178.6   
347990                               179.8   
347991                               179.4   
347992                               180.6   
347993                               180.2   
...                                    ...   
350475                               158.7   
350476                               154.9   
350477                               159.0   
350478                               152.2   
350479                               147.1   

        Energie geleverd aan de motor sinds reset (J)  \
347989                                          96685   
347990                                          96686   
347991                                          96688   
347992                                          96689   
347993                                          96691   
...                                               ...   
350475                                         100200   
350476                                         100201   
350477                                         100203   
350478                                         100204   
350479                                         100205   

        Spanning aan de ingang van motordriver (V)  \
347989                                      27.494   
347990                                      27.493   
347991                                      27.492   
347992                                      27.491   
347993                                      27.489   
...                                            ...   
350475                                      25.893   
350476                                     

In [23]:
#Bepalen hoeveel waardes van h we nodig hebben
getallen_tussen_rechtestuk_echt = []

# Calculate the number of points in each straight section
for i in range(0, len(rechtestuk_rijen_hoogte) - 1, 2):
    lengtes_rechte_stuk_echt = rechtestuk_rijen_hoogte[i + 1] - rechtestuk_rijen_hoogte[i]
    getallen_tussen_rechtestuk_echt.append(lengtes_rechte_stuk_echt)

print(getallen_tussen_rechtestuk_echt)

[3890]


In [62]:
# Dictionary to store datasets for each segment
#formule voor h, pas x_fit aan om het aantal datapunten te veranderen
x_fit = np.linspace(0, 206, 2491)
h = polynomial_7(x_fit)

# Plot the fit equation from x = 0 to x = 275
plt.figure(figsize=(10, 6))
plt.plot(x_fit, h, color='purple', linestyle='-', linewidth=2, label=f'Polynoom fit (graad {degree})')
plt.grid(visible=True, linestyle='--', alpha=0.7)
#Add fit equation to the plot
plt.text(
    0.05 * max(x_fit),
    0.85 * max(y_fit_7),
    fit_equation_7,
    color='purple',
    fontsize=10,
    bbox=dict(facecolor='white', alpha=0.7)
)
plt.xlabel('Cumulatieve Afstand (m)', fontsize=14)
plt.ylabel('Cumulatief Hoogteverschil (m)', fontsize=14)
plt.title('Fit voor hoogte profiel rechte stuk (2491 datapunten)', fontsize=16)

plt.show() 

df_h = pd.DataFrame({'hoogteverschil (m)': h})
# Voeg een kolom toe met het verschil in hoogte (delta h)
df_h['delta h (m)'] = df_h['hoogteverschil (m)'].diff().fillna(0)


In [70]:
print(df_ronde5.loc[347364])

Datalogger port                                                          5
Dataloggertijd, in s                                             5611.6496
Format header (>03|04)                                               03|04
Tijd sinds laatste herstart motordriver (s)                      1970.0708
Spanning over de motor (V)                                          19.109
Stroom door de motor (A)                                             8.047
Vermogen geleverd aan de motor (W)                                   165.6
Energie geleverd aan de motor sinds reset (J)                        95749
Spanning aan de ingang van motordriver (V)                          28.196
Stroom door de ingang van motordriver (A)                            6.321
Vermogen geleverd aan de hele motordriver (W)                        178.2
Energie geleverd aan de hele motordriver sinds reset (J)            103495
Motordriver temperatuur (C)                                          122.9
Motordriver-bord temperat

In [66]:
print(df_ronde6.loc[350479])

Datalogger port                                                          5
Dataloggertijd, in s                                             5639.0022
Format header (>03|04)                                               03|04
Tijd sinds laatste herstart motordriver (s)                      1997.4186
Spanning over de motor (V)                                          21.627
Stroom door de motor (A)                                             6.497
Vermogen geleverd aan de motor (W)                                   147.1
Energie geleverd aan de motor sinds reset (J)                       100205
Spanning aan de ingang van motordriver (V)                          25.889
Stroom door de ingang van motordriver (A)                             6.08
Vermogen geleverd aan de hele motordriver (W)                        157.4
Energie geleverd aan de hele motordriver sinds reset (J)            108149
Motordriver temperatuur (C)                                          123.0
Motordriver-bord temperat

In [71]:
df_h*-1

hoogteverschil (m)  delta h (m)
0              -0.053560    -0.000000
1              -0.053852    -0.000292
2              -0.054145    -0.000292
3              -0.054437    -0.000292
4              -0.054730    -0.000293
...                  ...          ...
2486           -1.026149    -0.000607
2487           -1.026757    -0.000607
2488           -1.027365    -0.000608
2489           -1.027974    -0.000609
2490           -1.028584    -0.000610

[2491 rows x 2 columns]

In [74]:
import pandas as pd

# Berekenen zwaartekracht
massa = 90  # Mass in kg
g = 9.81  # Gravitational acceleration in m/s²

import plotly.express as px
import pandas as pd

# Maak een nieuw dataframe voor het rechte stuk
rechte_stuk_ronde5_ronde6 = filtered_motordriver.loc[347364:350479]
# Initial speed in m/s
begin_snelheid = rechte_stuk_ronde5_ronde6["GPS speed, in m/s"]
print(f"Initial speed: {begin_snelheid} m/s")

# Bereken de initiële kinetische energie
initiele_kinetische_energie = 0.5 * massa * begin_snelheid**2
print(f"Initiële kinetische energie: {initiele_kinetische_energie} J")

# Maak een nieuwe lege DataFrame df_e met dezelfde index als df_h
df_e = pd.DataFrame(index=df_h.index)

# Bereken potentiële energie per punt op basis van de hoogteverschillen (neem absolute waarde van delta h)
initiele_potentiële_energie = massa * g * (df_h['hoogteverschil (m)'].iloc[0] - df_h['hoogteverschil (m)'].iloc[2490])
df_e['Potentiële Energie (J)'] = massa * g * df_h['delta h (m)'].abs()

# Bereken de omzetting van potentiële energie naar kinetische energie
df_e['Omzetting naar Kinetische Energie (J)'] = df_e['Potentiële Energie (J)']

# Bereken de cumulatieve som van de omzetting naar kinetische energie
df_e['Kinetische Energie Totaal (J)'] = df_e['Omzetting naar Kinetische Energie (J)'].cumsum()

# Voeg de initiële kinetische energie toe aan de hele kolom om de juiste startwaarde mee te nemen
df_e['Kinetische Energie Totaal (J)'] += initiele_kinetische_energie
df_e['Potentiële Energie Totaal (J)'] = df_e['Potentiële Energie (J)'][::-1].cumsum()[::-1]
df_e['Potentiële Energie Totaal (J)'] += initiele_potentiële_energie
df_e['Totale Energie (J)'] = df_e['Potentiële Energie Totaal (J)'] + df_e['Kinetische Energie Totaal (J)']

array_potentieel = df_e['Potentiële Energie Totaal (J)'].values
# Sla de potentiële energie op in een variabele voor gebruik in de tweede cel
potentiele_energie_uit_df_e = array_potentieel
print(potentiele_energie_uit_df_e)
# Print het resultaat voor controle
df_e


Initial speed: 347989    7.138889
347990    7.138889
347991    7.138889
347992    7.138889
347993    7.138889
            ...   
350475    7.916667
350476    7.916667
350477    7.916667
350478    7.916667
350479    7.916667
Name: GPS speed, in m/s, Length: 2491, dtype: float64 m/s
Initiële kinetische energie: 347989    2293.368056
347990    2293.368056
347991    2293.368056
347992    2293.368056
347993    2293.368056
             ...     
350475    2820.312500
350476    2820.312500
350477    2820.312500
350478    2820.312500
350479    2820.312500
Name: GPS speed, in m/s, Length: 2491, dtype: float64 J
[-1.25055521e-12 -1.25055521e-12 -2.58050917e-01 ... -8.59235216e+02
 -8.59772201e+02 -8.60309885e+02]


Potentiële Energie (J)  Omzetting naar Kinetische Energie (J)  \
0                   0.000000                               0.000000   
1                   0.258051                               0.258051   
2                   0.258142                               0.258142   
3                   0.258233                               0.258233   
4                   0.258324                               0.258324   
...                      ...                                    ...   
2486                0.535593                               0.535593   
2487                0.536288                               0.536288   
2488                0.536985                               0.536985   
2489                0.537684                               0.537684   
2490                0.538385                               0.538385   

      Kinetische Energie Totaal (J)  Potentiële Energie Totaal (J)  \
0                               NaN                  -1.250555e-12   
1                               NaN                  -1.250555e-12   
2                               NaN                  -2.580509e-01   
3                               NaN                  -5.161933e-01   
4                               NaN                  -7.744266e-01   
...                             ...                            ...   
2486                            NaN                  -8.581633e+02   
2487                            NaN                  -8.586989e+02   
2488                            NaN                  -8.592352e+02   
2489                            NaN                  -8.597722e+02   
2490                            NaN                  -8.603099e+02   

      Totale Energie (J)  
0                    NaN  
1                    NaN  
2                    NaN  
3                    NaN  
4                    NaN  
...                  ...  
2486                 NaN  
2487                 NaN  
2488                 NaN  
2489                 NaN  
2490                 NaN  

[2491 rows x 5 columns]

In [75]:
rechte_stuk_ronde5_ronde6

Datalogger port  Dataloggertijd, in s Format header (>03|04)  \
347989                5             5617.1410                  03|04   
347990                5             5617.1498                  03|04   
347991                5             5617.1586                  03|04   
347992                5             5617.1674                  03|04   
347993                5             5617.1761                  03|04   
...                 ...                   ...                    ...   
350475                5             5638.9669                  03|04   
350476                5             5638.9757                  03|04   
350477                5             5638.9845                  03|04   
350478                5             5638.9933                  03|04   
350479                5             5639.0022                  03|04   

        Tijd sinds laatste herstart motordriver (s)  \
347989                                    1975.5612   
347990                                    1975.5699   
347991                                    1975.5789   
347992                                    1975.5876   
347993                                    1975.5964   
...                                             ...   
350475                                    1997.3832   
350476                                    1997.3922   
350477                                    1997.4010   
350478                                    1997.4098   
350479                                    1997.4186   

        Spanning over de motor (V)  Stroom door de motor (A)  \
347989                      20.513                     8.113   
347990                      20.556                     8.133   
347991                      20.435                     8.116   
347992                      20.648                     8.120   
347993                      20.702                     8.080   
...                            ...                       ...   
350475                      22.547                     6.730   
350476                      22.042                     6.672   
350477                      22.190                     6.824   
350478                      21.737                     6.666   
350479                      21.627                     6.497   

        Vermogen geleverd aan de motor (W)  \
347989                               178.6   
347990                               179.8   
347991                               179.4   
347992                               180.6   
347993                               180.2   
...                                    ...   
350475                               158.7   
350476                               154.9   
350477                               159.0   
350478                               152.2   
350479                               147.1   

        Energie geleverd aan de motor sinds reset (J)  \
347989                                          96685   
347990                                          96686   
347991                                          96688   
347992                                          96689   
347993                                          96691   
...                                               ...   
350475                                         100200   
350476                                         100201   
350477                                         100203   
350478                                         100204   
350479                                         100205   

        Spanning aan de ingang van motordriver (V)  \
347989                                      27.494   
347990                                      27.493   
347991                                      27.492   
347992                                      27.491   
347993                                      27.489   
...                                            ...   
350475                                      25.893   
350476                                     

In [36]:
start_index = 18594 + 347989
end_index = start_index + 3890

# Bereken de kinetische energie met de gemeten snelheden van df_ronde6
gemeten_snelheden = df_ronde6.loc[start_index:end_index, "GPS speed, in m/s"]
df_e_kin = pd.DataFrame(index=gemeten_snelheden.index)  # Nieuwe DataFrame voor de gemeten kinetische energie
df_e_kin['Gemeten Snelheid (m/s)'] = gemeten_snelheden
df_e_kin['Kinetische Energie (J)'] = 0.5 * massa * df_e_kin['Gemeten Snelheid (m/s)']**2
df_e_kin['Potentiele Energie (J)'] = potentiele_energie_uit_df_e
df_e_kin['Totale Energie (J)'] = df_e_kin['Kinetische Energie (J)'] + df_e_kin['Potentiele Energie (J)']
values_totale_energie = df_e_kin['Totale Energie (J)'].values


In [31]:
# Reset de index van df_ronde6 zodat deze begint vanaf 0
df_ronde6_reset = df_ronde6.reset_index()

# Bereken de nieuwe start en eind indexen op basis van de numerieke positie
start_pos = df_ronde6_reset[df_ronde6_reset['index'] == start_index].index[0]  # Vind de nieuwe positie na reset
end_pos = start_pos + 3890

# Selecteer de waarden voor de nieuwe kolom
df_e['Energie geleverd aan de motor (J)'] = df_ronde6_reset.iloc[start_pos:end_pos + 1]['Energie geleverd aan de hele motordriver sinds reset (J)'].values
df_e

Potentiële Energie (J)  Omzetting naar Kinetische Energie (J)  \
0                   0.000000                               0.000000   
1                   0.561635                               0.561635   
2                   0.559376                               0.559376   
3                   0.557126                               0.557126   
4                   0.554884                               0.554884   
...                      ...                                    ...   
3886                0.362610                               0.362610   
3887                0.363568                               0.363568   
3888                0.364532                               0.364532   
3889                0.365501                               0.365501   
3890                0.366475                               0.366475   

      Kinetische Energie Totaal (J)  Potentiële Energie Totaal (J)  \
0                       3315.312500                    2152.776037   
1                       3315.874135                    2152.776037   
2                       3316.433511                    2152.214402   
3                       3316.990637                    2151.655026   
4                       3317.545521                    2151.097900   
...                             ...                            ...   
3886                    4390.240442                    1078.210704   
3887                    4390.604010                    1077.848094   
3888                    4390.968542                    1077.484526   
3889                    4391.334043                    1077.119994   
3890                    4391.700518                    1076.754493   

      Totale Energie (J)  Energie geleverd aan de motor (J)  
0            5468.088537                             120100  
1            5468.650171                             120100  
2            5468.647913                             120100  
3            5468.645662                             120100  
4            5468.643421                             120100  
...                  ...                                ...  
3886         5468.451146                             120079  
3887         5468.452105                             120079  
3888         5468.453068                             120079  
3889         5468.454037                             120079  
3890         5468.455012                             120079  

[3891 rows x 6 columns]

In [32]:
print(df_e.index.equals(df_e_kin.index))


False


In [40]:
df_e

Potentiële Energie (J)  Omzetting naar Kinetische Energie (J)  \
0                   0.000000                               0.000000   
1                   0.561635                               0.561635   
2                   0.559376                               0.559376   
3                   0.557126                               0.557126   
4                   0.554884                               0.554884   
...                      ...                                    ...   
3886                0.362610                               0.362610   
3887                0.363568                               0.363568   
3888                0.364532                               0.364532   
3889                0.365501                               0.365501   
3890                0.366475                               0.366475   

      Kinetische Energie Totaal (J)  Potentiële Energie Totaal (J)  \
0                       3315.312500                    2152.776037   
1                       3315.874135                    2152.776037   
2                       3316.433511                    2152.214402   
3                       3316.990637                    2151.655026   
4                       3317.545521                    2151.097900   
...                             ...                            ...   
3886                    4390.240442                    1078.210704   
3887                    4390.604010                    1077.848094   
3888                    4390.968542                    1077.484526   
3889                    4391.334043                    1077.119994   
3890                    4391.700518                    1076.754493   

      Totale Energie (J)  Energie geleverd aan de motor (J)  \
0            5468.088537                             120100   
1            5468.650171                             120100   
2            5468.647913                             120100   
3            5468.645662                             120100   
4            5468.643421                             120100   
...                  ...                                ...   
3886         5468.451146                             120079   
3887         5468.452105                             120079   
3888         5468.453068                             120079   
3889         5468.454037                             120079   
3890         5468.455012                             120079   

      Delta Energie geleverd aan de motor (J)  Gesommeerde Delta Energie (J)  \
0                                         0.0                            0.0   
1                                         0.0                            0.0   
2                                         0.0                            0.0   
3                                         0.0                            0.0   
4                                         0.0                            0.0   
...                                       ...                            ...   
3886                                      0.0                          -21.0   
3887                                      0.0                          -21.0   
3888                                      0.0                          -21.0   
3889                                      0.0                          -21.0   
3890                                      0.0                          -21.0   

      Totale theoretische energie (J)  Weerstand (J)  
0                         5468.088537   -2152.776037  
1                         5425.310759   -2109.436624  
2                         5424.749124   -2108.315613  
3                         5424.189748   -2107.199111  
4                         5423.632622   -2106.087101  
...                               ...            ...  
3886                      3800.432926     589.807516  
3887                      3800.070317     590.533694  
3888                      3799.706748     591.261794  
3889                      3799.342216     59

In [105]:
x= np.linspace(0,275.5,3891)

# Bereken de delta van de geleverde energie tussen opeenvolgende rijen
df_e['Delta Energie geleverd aan de motor (J)'] = df_e['Energie geleverd aan de motor (J)'].diff().fillna(0)

# Bereken de gesommeerde waarde van de delta energie over alle rijen
df_e['Gesommeerde Delta Energie (J)'] = df_e['Delta Energie geleverd aan de motor (J)'].cumsum()
df_e['Totale theoretische energie (J)'] = values_totale_energie
df_e['Weerstand (J)'] = df_e['Totale Energie (J)']-df_e['Totale theoretische energie (J)']

df_e['Delta weerstand (J)'] = df_e['Weerstand (J)'].diff().fillna(0)

df_e['x (m)'] = x

# Bereken de kracht als negatieve gradiënt van de potentiële energie (Weerstand) ten opzichte van positie (x)
df_e['F (N)'] = np.gradient(df_e['Weerstand (J)'], df_e['x (m)'])
# Print de eerste paar rijen van df_e om de nieuwe kolommen te bekijken
df_e


Potentiële Energie (J)  Omzetting naar Kinetische Energie (J)  \
0                   0.000000                               0.000000   
1                   0.561635                               0.561635   
2                   0.559376                               0.559376   
3                   0.557126                               0.557126   
4                   0.554884                               0.554884   
...                      ...                                    ...   
3886                0.362610                               0.362610   
3887                0.363568                               0.363568   
3888                0.364532                               0.364532   
3889                0.365501                               0.365501   
3890                0.366475                               0.366475   

      Kinetische Energie Totaal (J)  Potentiële Energie Totaal (J)  \
0                       3315.312500                    2152.776037   
1                       3315.874135                    2152.776037   
2                       3316.433511                    2152.214402   
3                       3316.990637                    2151.655026   
4                       3317.545521                    2151.097900   
...                             ...                            ...   
3886                    4390.240442                    1078.210704   
3887                    4390.604010                    1077.848094   
3888                    4390.968542                    1077.484526   
3889                    4391.334043                    1077.119994   
3890                    4391.700518                    1076.754493   

      Totale Energie (J)  Energie geleverd aan de motor (J)  \
0            5468.088537                             120100   
1            5468.650171                             120100   
2            5468.647913                             120100   
3            5468.645662                             120100   
4            5468.643421                             120100   
...                  ...                                ...   
3886         5468.451146                             120079   
3887         5468.452105                             120079   
3888         5468.453068                             120079   
3889         5468.454037                             120079   
3890         5468.455012                             120079   

      Delta Energie geleverd aan de motor (J)  Gesommeerde Delta Energie (J)  \
0                                         0.0                            0.0   
1                                         0.0                            0.0   
2                                         0.0                            0.0   
3                                         0.0                            0.0   
4                                         0.0                            0.0   
...                                       ...                            ...   
3886                                      0.0                          -21.0   
3887                                      0.0                          -21.0   
3888                                      0.0                          -21.0   
3889                                      0.0                          -21.0   
3890                                      0.0                          -21.0   

      Totale theoretische energie (J)  Weerstand (J)  Delta weerstand (J)  \
0                         5468.088537       0.000000             0.000000   
1                         5425.310759      43.339413            43.339413   
2                         5424.749124      43.898789             0.559376   
3                         5424.189748      44.455915             0.557126   
4                         5423.632622      45.010799             0.554884   
...                               ...            ...                  ...   
3886                      3800.432926    1668.018220   

In [76]:
plt.figure(figsize=(10, 6))

plt.scatter(df_e['x (m)'], df_e['Delta weerstand (J)'])

# Labels en titel toevoegen
# plt.xlim(0,276)
# plt.xticks(np.arange(0, 276, 25))  # Stel de x-as in stappen van 25
plt.xlabel('x (m)')
plt.ylabel('Weerstand (J)')
plt.title('Weerstand (J) tegen afstand (uitrollend)')
# plt.legend()
plt.grid(True)

# Toon de grafiek
plt.show()

In [78]:
# Eerstegraads fit berekenen
coefs = np.polyfit(x, df_e['Weerstand (J)'], 1)  # '1' betekent een lineaire (eerstegraads) fit
fit_line = np.poly1d(coefs)

# Plot maken
plt.figure(figsize=(10, 6))

# Scatterplot
plt.scatter(x, df_e['Weerstand (J)'], label='Data')

# De eerstegraads fit plotten
plt.plot(x, fit_line(x), color='red', linestyle='--', label=f'Fit: y = {coefs[0]:.2f}x + {coefs[1]:.2f}')

# Labels en titel toevoegen
plt.xlim(0, 276)
plt.xticks(np.arange(0, 276, 25))  # Stel de x-as in stappen van 25 in
plt.xlabel('x (m)')
plt.ylabel('Weerstand (J)')
plt.title('Weerstand tegen snelheid (uitrollend)')
plt.legend()
plt.grid(True)

# Toon de grafiek
plt.show()

In [109]:
# Eerstegraads fit berekenen
coefs = np.polyfit(df_e_kin['Gemeten Snelheid (m/s)'], df_e['F (N)'], 1)  # '1' betekent een lineaire (eerstegraads) fit
fit_line = np.poly1d(coefs)

# Plot maken
plt.figure(figsize=(10, 6))

# Scatterplot
plt.scatter(df_e_kin['Gemeten Snelheid (m/s)'], abs(df_e['F (N)']), label='Data')

# De eerstegraads fit plotten
plt.plot(df_e_kin['Gemeten Snelheid (m/s)'], fit_line(df_e_kin['Gemeten Snelheid (m/s)']), color='red', linestyle='--', label=f'Fit: y = {coefs[0]:.2f}x + {coefs[1]:.2f}')

# Labels en titel toevoegen
# plt.xlim(0, 276)
# plt.xticks(np.arange(0, 276, 25))  # Stel de x-as in stappen van 25 in
plt.xlabel('v (m/s)')
plt.ylabel('F (N)')
plt.title('Weerstand tegen snelheid (uitrollend)')
plt.legend()
plt.grid(True)

# Toon de grafiek
plt.show()

In [103]:
import numpy as np
import matplotlib.pyplot as plt

# Filter de gegevens vanaf rij 1970
start_index = 1765
x_filtered = x[start_index:]
y_filtered = df_e['Weerstand (J)'][start_index:]
snelheid_filtered = df_e_kin['Gemeten Snelheid (m/s)'][start_index:]

# Eerstegraads fit berekenen voor de gefilterde gegevens
coefs = np.polyfit(snelheid_filtered, y_filtered, 1)  # '1' betekent een lineaire (eerstegraads) fit
fit_line = np.poly1d(coefs)

# Plot maken
plt.figure(figsize=(10, 6))

# Scatterplot
plt.scatter(snelheid_filtered, y_filtered, label='Data')

# De eerstegraads fit plotten
plt.plot(snelheid_filtered, fit_line(snelheid_filtered), color='red', linestyle='--', label=f'Fit: y = {coefs[0]:.2f}x + {coefs[1]:.2f}')

# Labels en titel toevoegen
# plt.xlim(x_filtered.min(), x_filtered.max())
# plt.xticks(np.arange(x_filtered.min(), x_filtered.max(), 25))  # Stel de x-as in stappen van 25 in
plt.xlabel('V (m/s)')
plt.ylabel('Weerstand (J)')
plt.title('Weerstand tegen snelheid (uitrollend)')
plt.legend()
plt.grid(True)

# Toon de grafiek
plt.show()


In [ ]:
import numpy as np
import matplotlib.pyplot as plt

# Filter de gegevens vanaf rij 1970
start_index = 1765
x_filtered = x[start_index:]
y_filtered = df_e['Weerstand (J)'][start_index:]
snelheid_filtered = df_e_kin['Gemeten Snelheid (m/s)'][start_index:]

# Eerstegraads fit berekenen voor de gefilterde gegevens
coefs = np.polyfit(snelheid_filtered, y_filtered, 1)  # '1' betekent een lineaire (eerstegraads) fit
fit_line = np.poly1d(coefs)

# Plot maken
plt.figure(figsize=(10, 6))

# Scatterplot
plt.scatter(snelheid_filtered, y_filtered, label='Data')

# De eerstegraads fit plotten
plt.plot(snelheid_filtered, fit_line(snelheid_filtered), color='red', linestyle='--', label=f'Fit: y = {coefs[0]:.2f}x + {coefs[1]:.2f}')

# Labels en titel toevoegen
# plt.xlim(x_filtered.min(), x_filtered.max())
# plt.xticks(np.arange(x_filtered.min(), x_filtered.max(), 25))  # Stel de x-as in stappen van 25 in
plt.xlabel('V (m/s)')
plt.ylabel('Weerstand (J)')
plt.title('Weerstand tegen snelheid (uitrollend)')
plt.legend()
plt.grid(True)

# Toon de grafiek
plt.show()


In [99]:
import numpy as np
import matplotlib.pyplot as plt

# Gegevens filteren voor x >= 125
mask = x >= 125
x_filtered = x[mask]
y_filtered = df_e['Weerstand (J)'][mask]

# Index bepalen van de eerste rij waar x >= 125
start_index = np.where(mask)[0][0]

print(f"Eerste rij met x >= 125 is rij: {start_index}")

# Eerstegraads fit berekenen voor de gefilterde gegevens
coefs = np.polyfit(x_filtered, y_filtered, 1)  # '1' betekent een lineaire (eerstegraads) fit
fit_line = np.poly1d(coefs)

# Plot maken
plt.figure(figsize=(10, 6))

# Scatterplot
plt.scatter(x_filtered, y_filtered, label='Data')

# De eerstegraads fit plotten
plt.plot(x_filtered, fit_line(x_filtered), color='red', linestyle='--', label=f'Fit: y = {coefs[0]:.2f}x + {coefs[1]:.2f}')

# Labels en titel toevoegen
plt.xlim(125, 276)
plt.xticks(np.arange(125, 276, 25))  # Stel de x-as in stappen van 25 in
plt.xlabel('V (m/s)')
plt.ylabel('Weerstand (J)')
plt.title('Weerstand tegen snelheid (uitrollend)')
plt.legend()
plt.grid(True)

# Toon de grafiek
plt.show()


Eerste rij met x >= 125 is rij: 1765


In [86]:
df_e_kin

Gemeten Snelheid (m/s)  Kinetische Energie (J)  \
366583                8.583333             3315.312500   
366584                8.527778             3272.534722   
366585                8.527778             3272.534722   
366586                8.527778             3272.534722   
366587                8.527778             3272.534722   
...                        ...                     ...   
370469                7.777778             2722.222222   
370470                7.777778             2722.222222   
370471                7.777778             2722.222222   
370472                7.777778             2722.222222   
370473                7.777778             2722.222222   

        Potentiele Energie (J)  Totale Energie (J)  
366583             2152.776037         5468.088537  
366584             2152.776037         5425.310759  
366585             2152.214402         5424.749124  
366586             2151.655026         5424.189748  
366587             2151.097900         5423.632622  
...                        ...                 ...  
370469             1078.210704         3800.432926  
370470             1077.848094         3800.070317  
370471             1077.484526         3799.706748  
370472             1077.119994         3799.342216  
370473             1076.754493         3798.976716  

[3891 rows x 4 columns]

In [88]:
# Eerstegraads fit berekenen
coefs = np.polyfit(x, df_e['Weerstand (J)'], 1)  # '1' betekent een lineaire (eerstegraads) fit
fit_line = np.poly1d(coefs)

# Plot maken
plt.figure(figsize=(10, 6))

# Scatterplot
plt.scatter(df_e_kin['Gemeten Snelheid (m/s)'], df_e['Weerstand (J)'], label='Data')

# De eerstegraads fit plotten
plt.plot(x, fit_line(x), color='red', linestyle='--', label=f'Fit: y = {coefs[0]:.2f}x + {coefs[1]:.2f}')

# Labels en titel toevoegen
plt.xlim(0, 276)
plt.xticks(np.arange(0, 276, 25))  # Stel de x-as in stappen van 25 in
plt.xlabel('x (m)')
plt.ylabel('Weerstand (J)')
plt.title('Weerstand tegen snelheid (uitrollend)')
plt.legend()
plt.grid(True)

# Toon de grafiek
plt.show()

In [89]:

# Gegevens filteren voor x >= 125
mask = x >= 125
x_filtered = x[mask]
y_filtered = df_e['Weerstand (J)'][mask]

# Eerstegraads fit berekenen voor de gefilterde gegevens
coefs = np.polyfit(x_filtered, y_filtered, 1)  # '1' betekent een lineaire (eerstegraads) fit
fit_line = np.poly1d(coefs)

# Plot maken
plt.figure(figsize=(10, 6))

# Scatterplot
plt.scatter(x_filtered, y_filtered, label='Data')

# De eerstegraads fit plotten
plt.plot(x_filtered, fit_line(x_filtered), color='red', linestyle='--', label=f'Fit: y = {coefs[0]:.2f}x + {coefs[1]:.2f}')

# Labels en titel toevoegen
plt.xlim(125, 276)
plt.xticks(np.arange(125, 276, 25))  # Stel de x-as in stappen van 25 in
plt.xlabel('x (m)')
plt.ylabel('Weerstand (J)')
plt.title('Weerstand tegen snelheid (uitrollend)')
plt.legend()
plt.grid(True)

# Toon de grafiek
plt.show()


In [53]:
x = np.linspace(0, 275.5, 3891)
plt.figure(figsize=(10, 6))

plt.scatter(x, df_e['Gesommeerde Delta Energie (J)'], label='Energie geleverd aan motordriver (Gemeten)', color='g')
# Labels en titel toevoegen
plt.xlim(0, 276)
plt.xticks(np.arange(0, 276, 25))  # Stel de x-as in stappen van 25
plt.xlabel('Afgelegde Afstand (m)')
plt.ylabel('Energie (J)')
plt.title('Energie geleverd aan motordriver (meetdata) over Afgelegde Afstand met delta h van 1.2 m (uitrollend)')
plt.legend()
plt.grid(True)

# Toon de grafiek
plt.show()

TypeError: scatter() missing 2 required positional arguments: 'x' and 'y'

In [36]:
#Plot geleverde energie aan motordriver erbij
# Maak de x-as voor de afgelegde afstand
x = np.linspace(0, 275.5, 3891)

# Plot de kinetische energie en de gesommeerde delta-energie tegen de afgelegde afstand
plt.figure(figsize=(10, 6))
plt.plot(x, df_e['Kinetische Energie Totaal (J)'], label='Kinetische Energie in situatie zonder weerstand (berekend)')
plt.scatter(x, df_e_kin['Kinetische Energie (J)'], label='Kinetische Energie (Berekend uit gemeten snelheid)', color='r')
plt.scatter(x, df_e['Gesommeerde Delta Energie (J)'], label='Energie geleverd aan motordriver (Gemeten)', color='g')

# Labels en titel toevoegen
plt.xlim(0, 276)
plt.xticks(np.arange(0, 276, 25))  # Stel de x-as in stappen van 25
plt.xlabel('Afgelegde Afstand (m)')
plt.ylabel('Energie (J)')
plt.title('Kinetische Energie en Gesommeerde Delta Energie over Afgelegde Afstand met delta h van 1.2 m (uitrollend)')
plt.legend()
plt.grid(True)

# Toon de grafiek
plt.show()

In [37]:
# Stel massa, zwaartekracht, en rolweerstandscoëfficiënt in
massa = 90  # Massa in kg
g = 9.81  # Zwaartekrachtversnelling in m/s²
C_r = 0.006  # Rolweerstandscoëfficiënt

# Definieer de x-as als linspace (afgelegde afstand in meters)
x = np.linspace(0, 275.5, 3891)  # 3891 stappen over een afstand van 275.5 meter

# Stel de horizontale afstand (\Delta x) per stap in (gebruik linspace met gelijke afstanden)
delta_x = x[1] - x[0]  # Afstand tussen opeenvolgende meetpunten

# Bereken de hellingshoek per stap op basis van hoogteverschil en horizontale afstand
df_e['Hoek (rad)'] = np.arctan(df_h['delta h (m)'] / delta_x)

# Bereken de normaalkracht per rij rekening houdend met de hellingshoek
df_e['Normaalkracht (N)'] = massa * g * np.cos(df_e['Hoek (rad)'])

# Bereken de rolweerstandskracht per rij met de formule: R_rol = F_n * C_r
df_e['Rolweerstand (N)'] = df_e['Normaalkracht (N)'] * C_r

# Bereken de energieverlies door rolweerstand per stap (E_rol = F_rol * delta_x)
df_e['Energieverlies door rolweerstand (J)'] = df_e['Rolweerstand (N)'] * delta_x

# Bereken de cumulatieve energieverlies door rolweerstand
df_e['Cumulatieve Energieverlies door rolweerstand (J)'] = df_e['Energieverlies door rolweerstand (J)'].cumsum()

df_e

Potentiële Energie (J)  Omzetting naar Kinetische Energie (J)  \
0                   0.000000                               0.000000   
1                   0.561635                               0.561635   
2                   0.559376                               0.559376   
3                   0.557126                               0.557126   
4                   0.554884                               0.554884   
...                      ...                                    ...   
3886                0.362610                               0.362610   
3887                0.363568                               0.363568   
3888                0.364532                               0.364532   
3889                0.365501                               0.365501   
3890                0.366475                               0.366475   

      Kinetische Energie Totaal (J)  Potentiële Energie Totaal (J)  \
0                       3315.312500                    2152.776037   
1                       3315.874135                    2152.776037   
2                       3316.433511                    2152.214402   
3                       3316.990637                    2151.655026   
4                       3317.545521                    2151.097900   
...                             ...                            ...   
3886                    4390.240442                    1078.210704   
3887                    4390.604010                    1077.848094   
3888                    4390.968542                    1077.484526   
3889                    4391.334043                    1077.119994   
3890                    4391.700518                    1076.754493   

      Totale Energie (J)  Energie geleverd aan de motor (J)  \
0            5468.088537                             120100   
1            5468.650171                             120100   
2            5468.647913                             120100   
3            5468.645662                             120100   
4            5468.643421                             120100   
...                  ...                                ...   
3886         5468.451146                             120079   
3887         5468.452105                             120079   
3888         5468.453068                             120079   
3889         5468.454037                             120079   
3890         5468.455012                             120079   

      Delta Energie geleverd aan de motor (J)  Gesommeerde Delta Energie (J)  \
0                                         0.0                            0.0   
1                                         0.0                            0.0   
2                                         0.0                            0.0   
3                                         0.0                            0.0   
4                                         0.0                            0.0   
...                                       ...                            ...   
3886                                      0.0                          -21.0   
3887                                      0.0                          -21.0   
3888                                      0.0                          -21.0   
3889                                      0.0                          -21.0   
3890                                      0.0                          -21.0   

      Hoek (rad)  Normaalkracht (N)  Rolweerstand (N)  \
0       0.000000         882.900000          5.297400   
1      -0.008982         882.864388          5.297186   
2      -0.008946         882.864674          5.297188   
3      -0.008910         882.864957          5.297190   
4      -0.008874         882.865239          5.297191   
...          ...                ...               ...   
3886   -0.005799         882.885155          5.297311   
3887   -0.005814         882.885076          5.297310   
3888   -0.005830         882.884997          5.297310   
3889   -0.005845        

In [38]:
# Plot de cumulatieve kinetische energie en het energieverlies door rolweerstand tegen de afgelegde afstand
plt.figure(figsize=(10, 6))

# Plot de kinetische energie zonder weerstand
plt.plot(x, df_e['Totale Energie (J)'], label='Totale Energie in situatie zonder weerstand (berekend)', color='b')

# Plot de cumulatieve energieverlies door rolweerstand
plt.plot(x, df_e['Cumulatieve Energieverlies door rolweerstand (J)'], label='Cumulatieve Energieverlies door rolweerstand', color='g')

# Labels en titel toevoegen
plt.xlabel('Afgelegde Afstand (m)')
plt.ylabel('Energie (J)')
plt.title('Totale Energie en Energieverlies door Rolweerstand over Afgelegde Afstand')
plt.legend()
plt.grid(True)

# Toon de grafiek
plt.show()

df_e_kin

Gemeten Snelheid (m/s)  Kinetische Energie (J)  \
366583                8.583333             3315.312500   
366584                8.527778             3272.534722   
366585                8.527778             3272.534722   
366586                8.527778             3272.534722   
366587                8.527778             3272.534722   
...                        ...                     ...   
370469                7.777778             2722.222222   
370470                7.777778             2722.222222   
370471                7.777778             2722.222222   
370472                7.777778             2722.222222   
370473                7.777778             2722.222222   

        Potentiele Energie (J)  Totale Energie (J)  
366583             2152.776037         5468.088537  
366584             2152.776037         5425.310759  
366585             2152.214402         5424.749124  
366586             2151.655026         5424.189748  
366587             2151.097900         5423.632622  
...                        ...                 ...  
370469             1078.210704         3800.432926  
370470             1077.848094         3800.070317  
370471             1077.484526         3799.706748  
370472             1077.119994         3799.342216  
370473             1076.754493         3798.976716  

[3891 rows x 4 columns]

In [39]:
# Plot de cumulatieve kinetische energie en het energieverlies door rolweerstand tegen de afgelegde afstand
plt.figure(figsize=(10, 6))

# Plot de kinetische energie zonder weerstand
plt.plot(x, df_e['Totale Energie (J)'], label='Totale Energie theoretisch (berekend)', color='g')
plt.plot(x, df_e['Totale Energie (J)']-df_e['Cumulatieve Energieverlies door rolweerstand (J)'], label='Totale Energie in situatie met rolweerstand (berekend)', color='b')
plt.scatter(x, df_e_kin['Totale Energie (J)'], label='Totale (Berekend uit gemeten snelheid)', color='r')

# Labels en titel toevoegen
plt.xlabel('Afgelegde Afstand (m)')
plt.ylabel('Energie (J)')
plt.title('Totale Energie en Energieverlies door Rolweerstand over Afgelegde Afstand')
plt.legend()
plt.grid(True)

# Toon de grafiek
plt.show()


In [40]:
# Print de lengte van 'gemeten_snelheden' en 'df_e' om te controleren of ze gelijk zijn
print(f"Lengte van gemeten_snelheden: {len(gemeten_snelheden)}, Lengte van df_e: {len(df_e)}")

# Controleer of er NaN-waarden zijn in 'gemeten_snelheden'
if isinstance(gemeten_snelheden, pd.Series):
    print(f"Aantal NaN-waarden in gemeten_snelheden: {gemeten_snelheden.isna().sum()}")

# Voeg de snelheden toe aan df_e, ongeacht de index
df_e['Snelheid (m/s)'] = gemeten_snelheden.values  # Gebruik de waarden zonder de index mee te nemen

# Print de eerste paar rijen van df_e om te controleren of de snelheden zijn toegevoegd
print(df_e['Snelheid (m/s)'].head())


Lengte van gemeten_snelheden: 3891, Lengte van df_e: 3891
Aantal NaN-waarden in gemeten_snelheden: 0
0    8.583333
1    8.527778
2    8.527778
3    8.527778
4    8.527778
Name: Snelheid (m/s), dtype: float64


In [41]:

# Stel de luchtweerstandscoëfficiënt in
C_d = 0.09  # Luchtweerstandscoëfficiënt

# Stel een constante luchtdichtheid in (rho, in kg/m^3), typisch 1.225 voor droge lucht op zeeniveau
rho = 1.225  # kg/m^3

# Stel de frontale oppervlakte van de auto in (in m²) als voorbeeldwaarde
A = 0.279  # Frontale oppervlakte in m² (typische waarde voor een auto)

# Werk opnieuw met de x-as als linspace voor de afgelegde afstand
x = np.linspace(0, 275.5, 3891)  # 3891 stappen over een afstand van 275.5 meter
df_e['Afstand (m)'] = x

# Bereken de luchtweerstandskracht per stap (F_lucht = 0.5 * C_d * rho * A * v^2) met de bijgewerkte afstand
df_e['Luchtweerstand (N)'] = 0.5 * C_d * rho * A * df_e['Snelheid (m/s)']**2

# Bereken het energieverlies door luchtweerstand per stap opnieuw (E_lucht = F_lucht * delta_x)
df_e['Energieverlies door luchtweerstand (J)'] = df_e['Luchtweerstand (N)'] * delta_x

# Bereken de cumulatieve energieverlies door luchtweerstand opnieuw
df_e['Cumulatieve Energieverlies door luchtweerstand (J)'] = df_e['Energieverlies door luchtweerstand (J)'].cumsum()

# Print de eerste paar rijen van df_e om de nieuwe kolommen te bekijken
df_e


Potentiële Energie (J)  Omzetting naar Kinetische Energie (J)  \
0                   0.000000                               0.000000   
1                   0.561635                               0.561635   
2                   0.559376                               0.559376   
3                   0.557126                               0.557126   
4                   0.554884                               0.554884   
...                      ...                                    ...   
3886                0.362610                               0.362610   
3887                0.363568                               0.363568   
3888                0.364532                               0.364532   
3889                0.365501                               0.365501   
3890                0.366475                               0.366475   

      Kinetische Energie Totaal (J)  Potentiële Energie Totaal (J)  \
0                       3315.312500                    2152.776037   
1                       3315.874135                    2152.776037   
2                       3316.433511                    2152.214402   
3                       3316.990637                    2151.655026   
4                       3317.545521                    2151.097900   
...                             ...                            ...   
3886                    4390.240442                    1078.210704   
3887                    4390.604010                    1077.848094   
3888                    4390.968542                    1077.484526   
3889                    4391.334043                    1077.119994   
3890                    4391.700518                    1076.754493   

      Totale Energie (J)  Energie geleverd aan de motor (J)  \
0            5468.088537                             120100   
1            5468.650171                             120100   
2            5468.647913                             120100   
3            5468.645662                             120100   
4            5468.643421                             120100   
...                  ...                                ...   
3886         5468.451146                             120079   
3887         5468.452105                             120079   
3888         5468.453068                             120079   
3889         5468.454037                             120079   
3890         5468.455012                             120079   

      Delta Energie geleverd aan de motor (J)  Gesommeerde Delta Energie (J)  \
0                                         0.0                            0.0   
1                                         0.0                            0.0   
2                                         0.0                            0.0   
3                                         0.0                            0.0   
4                                         0.0                            0.0   
...                                       ...                            ...   
3886                                      0.0                          -21.0   
3887                                      0.0                          -21.0   
3888                                      0.0                          -21.0   
3889                                      0.0                          -21.0   
3890                                      0.0                          -21.0   

      Hoek (rad)  Normaalkracht (N)  Rolweerstand (N)  \
0       0.000000         882.900000          5.297400   
1      -0.008982         882.864388          5.297186   
2      -0.008946         882.864674          5.297188   
3      -0.008910         882.864957          5.297190   
4      -0.008874         882.865239          5.297191   
...          ...                ...               ...   
3886   -0.005799         882.885155          5.297311   
3887   -0.005814         882.885076          5.297310   
3888   -0.005830         882.884997          5.297310   
3889   -0.005845        

In [42]:
# Plot de cumulatieve kinetische energie en het energieverlies door rolweerstand tegen de afgelegde afstand
plt.figure(figsize=(10, 6))

# Plot de kinetische energie zonder weerstand
plt.plot(x, df_e['Totale Energie (J)'], label='Totale Energie theoretisch (berekend)', color='g')
plt.plot(x, df_e['Totale Energie (J)']-df_e['Cumulatieve Energieverlies door rolweerstand (J)'], label='Totale Energie in situatie met rolweerstand (berekend)', color='b')
plt.plot(x, df_e['Totale Energie (J)']-df_e['Cumulatieve Energieverlies door rolweerstand (J)']-df_e['Cumulatieve Energieverlies door luchtweerstand (J)'], label='Totale Energie in situatie met rolweerstand en luchtweerstand (berekend)', color='y')
plt.plot(x, df_e['Totale Energie (J)']-df_e['Cumulatieve Energieverlies door luchtweerstand (J)'], label='Totale Energie in situatie met luchtweerstand (berekend)', color='black')
plt.scatter(x, df_e_kin['Totale Energie (J)'], label='Totale Energie (Berekend uit gemeten snelheid)', color='r')

# Labels en titel toevoegen
plt.xlabel('Afgelegde Afstand (m)')
plt.ylabel('Energie (J)')
plt.title('Totale Energie en Energieverlies door alle weerstanden over Afgelegde Afstand')
plt.legend()
plt.grid(True)

# Toon de grafiek
plt.show()


In [43]:
plt.figure(figsize=(10, 6))

plt.plot(x, df_e['Totale Energie (J)']-df_e['Cumulatieve Energieverlies door rolweerstand (J)']-df_e['Cumulatieve Energieverlies door luchtweerstand (J)'], label='Totale Energie in situatie met rolweerstand en luchtweerstand (berekend)', color='y')
plt.scatter(x, df_e_kin['Totale Energie (J)'], label='Totale Energie (Berekend uit gemeten snelheid)', color='r')

# Labels en titel toevoegen
plt.xlabel('Afgelegde Afstand (m)')
plt.ylabel('Energie (J)')
plt.title('Totale Energie en Energieverlies door alle weerstanden over Afgelegde Afstand')
plt.legend()
plt.grid(True)

# Toon de grafiek
plt.show()